In [5]:
import os
import pickle
import pandas as pd
import numpy as np
from sklearn.metrics import accuracy_score, classification_report, f1_score, precision_score, recall_score
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from tqdm import tqdm  # For progress bars
from sklearn.utils.class_weight import compute_class_weight
from imblearn.over_sampling import SMOTE

# Helper function to calculate top-3 accuracy
def calculate_top3_accuracy(y_true, y_probs):
    top_3_preds = np.argsort(y_probs, axis=1)[:, -3:]
    matches = [y_true[i] in top_3_preds[i] for i in range(len(y_true))]
    return np.mean(matches)

# Helper function to calculate Threshold Accuracy
def calculate_threshold_accuracy(y_true, y_pred, threshold=1):
    return np.mean(np.abs(y_true - y_pred) <= threshold)

# Helper function to evaluate metrics
def evaluate_metrics(y_true, y_pred, y_probs=None, threshold=1):
    metrics = {
        'accuracy': accuracy_score(y_true, y_pred),
        'precision': precision_score(y_true, y_pred, average='weighted', zero_division=0),
        'recall': recall_score(y_true, y_pred, average='weighted', zero_division=0),
        'f1_score': f1_score(y_true, y_pred, average='weighted'),
        'threshold_accuracy': calculate_threshold_accuracy(y_true, y_pred, threshold),
        'classification_report': classification_report(y_true, y_pred, zero_division=0)
    }
    if y_probs is not None:
        metrics['top_3_accuracy'] = calculate_top3_accuracy(y_true, y_probs)
    return metrics

# Helper function to load dataset
def load_data(file_path):
    print(f"Loading data from: {file_path}")
    data = pd.read_csv(file_path)
    label_columns = [col for col in data.columns if "slider" in col]
    feature_columns = [col for col in data.columns if col not in label_columns + ["Timestamp", "participant_id"]]
    X = data[feature_columns]
    return X, label_columns, data

# Function to train models per label with class imbalance handling
def train_model_per_label(X_train, y_train, X_test, y_test, model_save_path, label_name, model_type="xgb"):
    model_file = os.path.join(model_save_path, f"{model_type}_{label_name}.pkl")
    if os.path.exists(model_file):
        print(f"Skipping {label_name} with {model_type}: Model already exists.")
        return None
    
    os.makedirs(model_save_path, exist_ok=True)
    y_train = y_train.astype(int)
    y_test = y_test.astype(int)
    X_train = X_train.to_numpy()
    X_test = X_test.to_numpy()
    
    all_classes = np.arange(11)
    unique_classes = np.unique(y_train)
    
    missing_classes = set(all_classes) - set(unique_classes)
    if missing_classes:
        print(f"Warning: Missing classes {missing_classes} in training data. Adding dummy samples.")
        for cls in missing_classes:
            X_train = np.vstack([X_train, X_train[0]])
            y_train = np.append(y_train, cls)
    
    class_weights = compute_class_weight("balanced", classes=all_classes, y=y_train)
    min_class_samples = min(np.bincount(y_train))
    
    if len(unique_classes) > 2 and min_class_samples >= 6:
        smote = SMOTE(sampling_strategy="auto", random_state=42)
        X_train, y_train = smote.fit_resample(X_train, y_train)
        print(f"Applied SMOTE for label {label_name}")
    else:
        print(f"Skipping SMOTE for {label_name} (min class has {min_class_samples} samples)")
    
    num_classes = len(all_classes)
    if model_type == "xgb":
        model = XGBClassifier(
            objective="multi:softmax",
            num_class=num_classes,
            eval_metric="mlogloss",
            use_label_encoder=False,
            scale_pos_weight=class_weights,
            tree_method="gpu_hist"
        )
    elif model_type == "lgbm":
        model = LGBMClassifier(
            objective="multiclass",
            num_class=num_classes,
            is_unbalance=True,
            num_leaves=15,
            min_data_in_leaf=5,
            max_depth=6,
            learning_rate=0.05,
            feature_fraction=0.8,
            bagging_fraction=0.8,
            bagging_freq=5,
            lambda_l1=0.5,
            lambda_l2=0.5,
            n_jobs=-1
        )
    else:
        raise ValueError("Unsupported model type")
    
    model.fit(X_train, y_train)
    y_pred = model.predict(X_test)
    y_probs = model.predict_proba(X_test) if hasattr(model, "predict_proba") else None
    
    with open(model_file, "wb") as f:
        pickle.dump(model, f)
    
    return evaluate_metrics(y_test, y_pred, y_probs)

# Main training loop
def train_all_models(data_dir, root_dir):
    results = []
    for data_type in ["pca", "scaled"]:
        for fold in tqdm(range(6), desc=f"Processing {data_type} Folds"):
            train_file = os.path.join(data_dir, f"fold_{fold}_train_{data_type}.csv")
            test_file = os.path.join(data_dir, f"fold_{fold}_test_{data_type}.csv")
            
            if not os.path.exists(train_file) or not os.path.exists(test_file):
                print(f"Skipping fold {fold}: Missing {data_type} train or test data")
                continue
            
            X_train, label_columns, train_data = load_data(train_file)
            X_test, _, test_data = load_data(test_file)
            
            for label_column in label_columns:
                y_train, y_test = train_data[label_column], test_data[label_column]
                fold_save_dir = os.path.join(root_dir, f"fold_{fold}", "models", data_type, label_column)
                os.makedirs(fold_save_dir, exist_ok=True)
                
                for model_type in ["xgb", "lgbm"]:
                    model_results = train_model_per_label(X_train, y_train, X_test, y_test, os.path.join(fold_save_dir, model_type), label_column, model_type)
                    if model_results:
                        results.append({"Fold": fold, "Label": label_column, "Model": model_type.upper(), "Data Type": data_type, **model_results})
    
    results_df = pd.DataFrame(results)
    results_df.to_csv("fold_transformed_LGBM_XGB_model_performance_results.csv", index=False)
    print("Model training results saved to fold_transformed_LGBM_XGB_model_performance_results.csv")

if __name__ == "__main__":
    data_dir = "folds_transformed"
    root_dir = "folds_transformed_LGBM_XGB_models"
    train_all_models(data_dir, root_dir)


Processing pca Folds:   0%|          | 0/6 [00:00<?, ?it/s]

Skipping fold 0: Missing pca train or test data
Loading data from: folds_transformed/fold_1_train_pca.csv
Loading data from: folds_transformed/fold_1_test_pca.csv
Applied SMOTE for label P1 (sliderNeutralPos)


/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning: [14:17:19] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning: [14:17:19] WARNING: /workspace/src/learner.cc:742: 
Parameters: { "scale_pos_weight" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning: [14:17:21] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)


Applied SMOTE for label P1 (sliderNeutralPos)
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] lambda_l2 is set=0.5, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.5
[LightGBM] [Warning] lambda_l1 is set=0.5, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.5
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] lambda_l2 is 

/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(


...

Skipping SMOTE for PRO3 (sliderNeutralPos) (min class has 1 samples)


/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning: [15:09:52] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning: [15:09:52] WARNING: /workspace/src/learner.cc:742: 
Parameters: { "scale_pos_weight" } are not used.

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.10/dist-packages/xgboost/core.py:160: UserWarning: [15:09:54] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)


Skipping SMOTE for PRO3 (sliderNeutralPos) (min class has 1 samples)
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] lambda_l2 is set=0.5, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.5
[LightGBM] [Warning] lambda_l1 is set=0.5, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.5
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] 

/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
Processing scaled Folds: 100%|██████████| 6/6 [36:24<00:00, 364.15s/it]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] feature_fraction is set=0.8, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8
[LightGBM] [Warning] lambda_l2 is set=0.5, reg_lambda=0.0 will be ignored. Current value: lambda_l2=0.5
[LightGBM] [Warning] lambda_l1 is set=0.5, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.5
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] min_data_in_leaf is set=5, min_child_samples=20 will be ignored. Current value: min_data_in_leaf=5
[LightGBM] [Warning] feature_fraction is set=0.8, cols